In [22]:
import pandas as pd
# from pandas_profiling import ProfileReport

from num2words import num2words
import re, unicodedata
# import contractions
from nltk import word_tokenize
from nltk.corpus import stopwords

from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.pipeline import Pipeline
from sklearn.base import BaseEstimator, TransformerMixin
import nltk

In [23]:
# %conda install -c conda-forge contractions

# Preparacion de ambiente

In [24]:
# Punkt permite separar un texto en frases.
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\ernes\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [25]:
# Descarga todas las palabras vacias, es decir, aquellas que no aportan nada al significado del texto
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\ernes\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [26]:
# Descarga de paquete WordNetLemmatizer, este es usado para encontrar el lema de cada palabra
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\ernes\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

# Exploracion de datos

In [27]:
df_raw = pd.read_excel('cat_6716.xlsx')

In [28]:
# Contar valores nulos
df_raw.isnull().sum()

Textos_espanol    0
sdg               0
dtype: int64

In [29]:
# Contar duplicados
df_raw.duplicated().sum()

0

In [30]:
df_raw.head()

Textos_espanol  sdg
0  Es importante destacar que, en un año de sequí...    6
1  Hay una gran cantidad de literatura sobre Aust...    6
2  Los procesos de descentralización, emprendidos...    6
3  Esto puede tener consecuencias sustanciales pa...    6
4  La función de beneficio también incorpora pará...    6

In [31]:
textos = df_raw.copy()
textos['Conteo'] = [len(x) for x in textos['Textos_espanol']]
textos['Moda'] = [max(set(x.split(' ')), key = x.split(' ').count) for x in textos['Textos_espanol']]
textos['Max'] = [[max([len(x) for x in i.split(' ')])][0] for i in textos['Textos_espanol']]
textos['Min'] = [[min([len(x) for x in i.split(' ')])][0] for i in textos['Textos_espanol']]

# Se realiza un perfilamiento de los datos con la libre pandas profiling
# ProfileReport(textos)

# Preparacion de datos

### Separar en datos de entrenamiento y prueba

In [32]:
X, Y = df_raw['Textos_espanol'], df_raw['sdg']
Y = Y.astype(int)
Y

0        6
1        6
2        6
3        6
4        6
        ..
2995    16
2996    16
2997    16
2998    16
2999    16
Name: sdg, Length: 3000, dtype: int32

In [33]:
X_train, X_test, Y_train, Y_test = train_test_split(X, Y, test_size=0.2, random_state=0)

In [34]:
X_train.shape, Y_train.shape


((2400,), (2400,))

In [35]:
X_test.shape, Y_test.shape

((600,), (600,))

In [36]:
X_train.head()

2370    Lograr el respeto de los derechos humanos por ...
1774    Diseño de proyectos sostenibles de electrifica...
731     En las partes españolas de las cuencas del Due...
271     Garantizar que los arreglos de gobernanza ayud...
1077    Además, a nivel de plantas y unidades, no hay ...
Name: Textos_espanol, dtype: object

#### **3.1 Limpieza de los datos**

https://medium.com/datos-y-ciencia/preprocesamiento-de-datos-de-texto-un-tutorial-en-python-5db5620f1767

In [37]:
class TextTransformer(BaseEstimator, TransformerMixin):
    """
    Se encarga de remover caracteres ascii, convertir a minúsculas, quitar puntuación y transformar números a letras
    """
    def fit(self, X, y=None):
        return self

    def transform(self, X):
        X = X.apply(lambda x: self.tokenize_and_process_text(x))
        return X

    def tokenize_and_process_text(self, text):
        tokens = word_tokenize(text, language='spanish')
        processed_tokens = [self.remove_non_ascii(token) for token in tokens]
        processed_tokens = [self.to_lowercase(token) for token in processed_tokens]
        processed_tokens = [self.remove_punctuation(token) for token in processed_tokens]
        processed_tokens = [self.replace_numbers(token) for token in processed_tokens]
        processed_tokens = [self.remove_stopwords(token) for token in processed_tokens]
        processed_text = ' '.join(processed_tokens)
        return processed_text

    def remove_non_ascii(self, word):
        return unicodedata.normalize('NFKD', word).encode('ascii', 'ignore').decode('utf-8', 'ignore')

    def to_lowercase(self, word):
        return word.lower()

    def remove_punctuation(self, word):
        return re.sub(r'[^\w\s]', '', word)

    def replace_numbers(self, word):
        if word.isdigit():
            return num2words(word, lang='es')
        return word    
    
    def remove_stopwords(self, word):
        stop_words = stopwords.words('spanish')
        if word in stop_words:
            return ''
        return word

In [38]:
class NormalizeTokens(BaseEstimator, TransformerMixin):
    """Hace lematización de las palabras"""

    def fit(self, X, y=None):
        return self
    
    def transform(self, X):
        X = X.apply(lambda x: self.lemmatize_text(x))
        return X
    
    def lemmatize_text(self, text):
        lemmatizer = nltk.stem.WordNetLemmatizer()
        tokens = word_tokenize(text, language='spanish')
        lemmatized_tokens = [lemmatizer.lemmatize(token) for token in tokens]
        lemmatized_text = ' '.join(lemmatized_tokens)
        return lemmatized_text

In [39]:
pipeline = Pipeline(
    [
        ("text_transformer", TextTransformer()),
        ("normalize_tokens", NormalizeTokens()),
        ("tfidf", TfidfVectorizer(stop_words=stopwords.words('spanish')))
    ]
)   
pipeline.fit(X_train, Y_train)

lograr
el
respeto
de
los
derechos
humanos
por
parte
de
las
empresas
no
requiere
hacer
la
eleccin

correcta

entre
leyes
duras
y
blandas

sino
establecer
una
arquitectura
para
sustentar
una
dialctica
constructiva
entre
las
dos

este
ensayo
argumenta
que
un
tratado
sobre
empresas
y
derechos
humanos
modelado
como
una
convencin
marco
y
centrado
inicialmente
en
los
principios
rectores
de
la
onu

ungp

por
sus
siglas
en
ingls

ofrece
tal
estructura
al
mismo
tiempo
que
evita
las
deficiencias
de
las
propuestas
de
tratados
presentadas
hasta
la
fecha

diseo
de
proyectos
sostenibles
de
electrificacin
rural
sin
conexin
a
la
red

principios
y
prcticas

washington

dc

disponible
en

http

siteresourcesworldbankorgextenergy2resourcesoffgridguidelines

low
carbon
energy
projects
for
development
in
subsaharan
africa

unveiling
the
potential

addressing
the
barriers

en
las
partes
espaolas
de
las
cuencas
del
duero
y
guadiana

respectivamente

el
92

y
el
88

de
la
extraccin
de
agua
es
para
uso
agrcola


Pipeline(steps=[('text_transformer', TextTransformer()),
                ('normalize_tokens', NormalizeTokens()),
                ('tfidf',
                 TfidfVectorizer(stop_words=['de', 'la', 'que', 'el', 'en', 'y',
                                             'a', 'los', 'del', 'se', 'las',
                                             'por', 'un', 'para', 'con', 'no',
                                             'una', 'su', 'al', 'lo', 'como',
                                             'más', 'pero', 'sus', 'le', 'ya',
                                             'o', 'este', 'sí', 'porque', ...]))])

# De aqui toca implementar pipe

In [40]:
# Pasar todos los caracteres Ã³ a o.
X_train = X_train.str.replace('Ã³', 'o')  

#### **3.2 Tokenización**

In [42]:
# df_raw['Message'] = df_raw['Message'].apply(contractions.fix) #Aplica la corrección de las contracciones

In [43]:
#Aplica la eliminación del ruido
X_train = X_train.apply(word_tokenize).apply(preprocessing) 
X_train.head()

KeyboardInterrupt: 

#### **3.3. Normalización**

In [ ]:
# install spacy
# TODO: Instalar spacy y correr la funcion de lematizacion
# %conda install -c conda-forge spacy

In [ ]:
from nltk.stem.snowball import SpanishStemmer
# import spacy
#TODO: Probar stemming vs lematizacion y ver cual funciona mejor
def stem_words_spanish(words):
    # Stem words in list of tokenized words (Spanish)
    stemmer = SpanishStemmer()
    stems = []
    for word in words:
        stem = stemmer.stem(word)
        stems.append(stem)
    return stems



def lemmatize_verbs_spanish(text):
    """Lemmatize verbs in a text (Spanish)"""
    nlp = spacy.load("es_core_news_sm")
    doc = nlp(text)
    lemmas = [token.lemma_ if token.pos_ == "VERB" else token.text for token in doc]
    return lemmas

X_train_stemmed = X_train.copy()
X_train_lematized = X_train.copy()
X_train_stemmed = X_train.apply(stem_words_spanish) #Aplica steming
X_train_lematized = X_train.apply(stem_words_spanish) #Aplica lematización 


In [ ]:
X_train_stemmed.head()

2370    [logr, respet, derech, human, part, empres, re...
1774    [disen, proyect, sosten, electrif, rural, cone...
731     [part, espanol, cuenc, duer, guadian, respect,...
271     [garantiz, arregl, gobern, ayud, moviliz, fina...
1077    [adem, nivel, plant, unidad, prueb, diferent, ...
Name: Textos_espanol, dtype: object

In [ ]:
X_train_lematized.head()

2370    [logr, respet, derech, human, part, empres, re...
1774    [disen, proyect, sosten, electrif, rural, cone...
731     [part, espanol, cuenc, duer, guadian, respect,...
271     [garantiz, arregl, gobern, ayud, moviliz, fina...
1077    [adem, nivel, plant, unidad, prueb, diferent, ...
Name: Textos_espanol, dtype: object

##### **3.4 Selección de campos**

Primero, se separa la variable predictora y los textos que se van a utilizar.

In [ ]:
# Transformación Term-frecuency times inverse Document-frecuency.
tf_idf = TfidfVectorizer()
X_tf_idf = tf_idf.fit_transform(X_train_lematized)
print(X_tf_idf.shape)
X_tf_idf.toarray()[0]

(3000, 11841)


array([0., 0., 0., ..., 0., 0., 0.])